In [ ]:
# import sys
# !conda install --yes --prefix {sys.prefix} -c conda-forge cvxpy

In [ ]:
import cvxpy as cp
import numpy as np
import scipy

In [ ]:
m_wet = 2000.0 # rocket wet mass [kg]
m_dry =  300.0 # rocket dry mass [kg]
thrust_max = 24000.0 # maximum thrust
ρ1 = 0.2 * thrust_max # lower bound on thrust
ρ2 = 0.8 * thrust_max # upper bound on thrust
α = 5e-4 # rocket specific impulse [s]
θ = np.deg2rad(30) # max thrust angle deviation from vertical [rad]
γ = np.deg2rad(15) # angle, measured from the horizontal, that defines the no-fly bounds [rad]
g = 3.71 # gravity [m/s2]
tf = 52.0 # duration of the simulation [s]
n_pts = 50 # number of points used in the discretization of time [-]

In [ ]:
# derived parameters
t = np.linspace(0.0, tf, n_pts) # time vector [s]
N = len(t)                      # number of unfixed control nodes (t_k = k Δt)
dt = t[1] - t[0]

In [ ]:
# initial state (x,y,x_dot,y_dot,z)
x0 = np.array([600.0, 1200.0, 50.0, -95.0, np.log(m_wet)])
# x0 = np.array([600.0, 1200.0, -50.0, -95.0, np.log(m_wet)])

In [ ]:
Ac = np.vstack((
        np.hstack((np.zeros((2, 2)), np.eye(2),         np.zeros((2, 1)))),
        np.hstack((np.zeros((2, 2)), np.zeros((2, 2)),  np.zeros((2, 1)))),
        np.zeros((1, 5))
     ))

Ad = scipy.linalg.expm(Ac * dt)

In [ ]:
def integrate_trapezoidal(f, a, b, n):
    retval = f(a) * 0.5 + f(b) * 0.5
    for k in range(1, n):
        retval = retval + f(a + k*(b-a)/n)
    retval = retval * (b - a)/ n
    return retval

Bc = np.vstack((
        np.hstack((np.zeros((2, 2)),   np.zeros((2, 1)))),
        np.hstack((np.eye(2),          np.zeros((2, 1)))),
        np.hstack((np.zeros((1, 2)),   np.reshape(np.array([-α]), (1, 1))))
    ))

Bd1 = integrate_trapezoidal(lambda s: np.matmul(scipy.linalg.expm(Ac*(dt-s)), Bc), 0.0, dt, 10000)
Bd2 = integrate_trapezoidal(lambda s: np.matmul(scipy.linalg.expm(Ac*(dt-s))*(s/dt), Bc), 0.0, dt, 10000)

In [ ]:
 # gravitational 3-vector [m/s2]
g3 = np.array([0.0, -g, 0.0])

def get_xk(Ad, Bd1, Bd2, η, x0, g3, k):
    xk = x0
    p_km1 = np.array([0.0,0.0,0.0])
    p_k = η[0:3]
    ind_low = 0
    for j in range(0,k):
        xk = np.matmul(Ad,xk) + np.matmul(Bd1, (p_km1 + g3)) + np.matmul(Bd2, (p_k - p_km1))
        p_km1 = p_k
        ind_low = min(ind_low+3, 3*(N+1))
        p_k = η[ind_low : ind_low+3]
    return xk


In [ ]:
# Create the cvx problem 
η = cp.Variable(3*N)

ω = np.tile(np.array([0,0,1]), N) # only minimize σ's

# minimize fuel consumption
objective = cp.Minimize(ω.T@η)
constraints = []

# thrust magnitude constraints
for k in range(0, N):
    j = 3*k
    constraints.append(cp.norm(η[j:j+2]) <= η[j+2])

# thrust cant angle constraints
for k in range(0, N):
    j = 3*k
    uy = η[j+1]
    σ = η[j+2]
    constraints.append(uy >= np.cos(θ) * σ)

# thrust slack variable lower and upper bounds
z0 = lambda k: np.log(m_wet - α*ρ2*dt*k)
z1 = lambda k: np.log(m_wet - α*ρ1*dt*k)
for k in range(0, N):
    j = 3*k
    σk = η[j+2]
    xk = get_xk(Ad, Bd1, Bd2, η, x0, g3, k)
    zk = xk[-1]

    a = ρ1 * np.exp(-z0(k))
    z0k = z0(k).item()
    z1k = z1(k).item()

    constraints.append(a * (1 - (zk-z0k) + 0.5*cp.square(zk-z0k)) <= σk)    
    constraints.append(σk <= ρ2 * np.exp(-z0k) * (1 - (zk-z0k)))

# glide angle constraints
for k in range(1, N):
    j = 3*k
    xk = get_xk(Ad, Bd1, Bd2, η, x0, g3, k)
    constraints.append(xk[1] >= np.tan(γ) * xk[0])

# terminal conditions
xf = get_xk(Ad, Bd1, Bd2, η, x0, g3, N)
constraints.append(xf[0:4] == [0,0,0,0])
constraints.append(xf[4] >= np.log(m_dry))

prob = cp.Problem(objective, constraints)

In [ ]:
result = prob.solve()
print(prob.status)

In [ ]:
# extract a solution
η_eval = η.value

xk = np.zeros((len(x0), len(t)))
for (i,k) in enumerate(range(0,N)):
    xk[:,i] = get_xk(Ad, Bd1, Bd2, η_eval, x0, g3, k)

xs = xk[0,:]
ys = xk[1,:]
us = xk[2,:]
vs = xk[3,:]
zs = xk[4,:]

mass = np.exp(zs)

u1 = η_eval[0::3]
u2 = η_eval[1::3]
σ = η_eval[2::3]

Tx = u1 * mass
Ty = u2 * mass
Γ = σ * mass
thrust_mag = [np.hypot(Tyi, Txi) for (Txi, Tyi) in zip(Tx, Ty)]
thrust_ang = [np.arctan2(Txi, Tyi) for (Txi, Tyi) in zip(Tx, Ty)]

In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt

In [ ]:
fig, ax = plt.subplots()
ax.plot(t, u1);
ax.plot(t, u2);
ax.legend(['u1', 'u2'])
plt.xlabel("time [s]")
plt.ylabel("massless thrust [N]")
fig.set_size_inches(12.0, 4.0)

In [ ]:
fig, ax = plt.subplots()
ax.plot([t[0], t[-1]], [0, 0], 'k');
ax.plot(t, Tx);
ax.plot(t, Ty);
ax.legend(['zero', 'Tx', 'Ty'])
plt.xlabel("time [s]")
plt.ylabel("thrust [N]")
fig.set_size_inches(12.0, 4.0)

In [ ]:
σ_lowerbound = [ρ1 * np.exp(-z0(k)) * (1 - (zs[k]-z0(k)) + 0.5*(zs[k] -z0(k))*(zs[k] -z0(k))) for k in range(0, N)]
σ_upperbound = [ρ2 * np.exp(-z0(k)) * (1 - (zs[k]-z0(k))) for k in range(0, N)]

fig, ax = plt.subplots()
ax.plot(t, σ);
ax.plot(t, σ_lowerbound, 'k');
ax.plot(t, σ_upperbound, 'k');
ax.legend(['sigma', 'lowerbound', 'upperbound'])
plt.xlabel("time [s]")
fig.set_size_inches(12.0, 4.0)

In [ ]:
fig, ax = plt.subplots()
ax.plot([t[0], t[-1]], [ρ1, ρ1], 'k');
ax.plot([t[0], t[-1]], [ρ2, ρ2], 'k');
ax.plot(t, thrust_mag);
ax.plot(t, Γ);
ax.legend(['lowerbound', 'upperbound', 'norm(T)', 'Gamma'])
plt.xlabel("time [s]")
plt.ylabel("thrust magnitude [N]")
fig.set_size_inches(12.0, 4.0)

In [ ]:
fig, ax = plt.subplots()
ax.plot([t[0], t[-1]], [m_wet, m_wet], 'k');
ax.plot([t[0], t[-1]], [m_dry, m_dry], 'k');
ax.plot(t, mass, 'g');
ax.legend(['wet mass', 'dry mass', 'mass'])
plt.xlabel("time [s]")
plt.ylabel("mass [kg]")
fig.set_size_inches(12.0, 4.0)

In [ ]:
# problem.constraints += uy >= cos(θ) * σ

fig, ax = plt.subplots()
ax.plot(t, u2 / σ);
ax.plot([t[0], t[-1]], [np.cos(θ), np.cos(θ)], 'k');
ax.legend(['thrust angle ratio', 'cos sigma'])
ax.set_ylim(0.0,1.1)
plt.xlabel("time [s]")
fig.set_size_inches(12.0, 6.0)

In [ ]:
fig, ax = plt.subplots()
ax.plot(t, np.rad2deg(thrust_ang));
ax.plot([t[0], t[-1]], [np.rad2deg(θ), np.rad2deg(θ)], 'k');
ax.plot([t[0], t[-1]], [-np.rad2deg(θ), -np.rad2deg(θ)], 'k');
ax.legend(['thrust angle', 'max thrust angle', 'min thrust angle'])
plt.xlabel("time [s]")
plt.ylabel("angle [deg]")
fig.set_size_inches(12.0, 6.0)

In [ ]:
fig, (ax1, ax2) = plt.subplots(2, 1)
ax1.plot(t, vs, 'm');
ax1.legend(['v [m/s]'])
ax2.plot([t[0], t[-1]], [0.0, 0.0], 'k');
ax2.plot(t, Ty, 'r');
ax2.legend(['zero', 'Ty [N]', ])
plt.xlabel("time [s]")
fig.set_size_inches(12.0, 6.0)

In [ ]:
fig, (ax1, ax2) = plt.subplots(2, 1)
ax1.plot(t, xs, 'b');
ax1.plot(t, ys, 'g');
ax1.legend(['x [m]', 'y [m]'])
ax2.plot(t, us, 'r');
ax2.plot(t, vs, 'm');
ax2.legend(['u [m/s]', 'v [m/s]'])
plt.xlabel("time [s]")
plt.ylabel("state")
fig.set_size_inches(12.0, 6.0)

In [ ]:
x_min = min(xs)
x_max = max(xs)
no_fly_pts = [x_min-100.0, 0.0, x_max+100.0]

fig, ax = plt.subplots()
ax.plot(xs, ys, 'o-');
ax.plot(no_fly_pts, [np.abs(x)*np.sin(γ) for x in no_fly_pts]);
ax.plot(no_fly_pts, [0.0 for x in no_fly_pts], 'k');
plt.xlabel("x [m]")
plt.ylabel("y [m]")
plt.title("Trajectory")
fig.set_size_inches(12.0, 6.0)